In [ ]:
from google.colab import files
uploaded = files.upload()


Saving inventory_forecasting.csv to inventory_forecasting.csv


In [ ]:
!pip install -q pandasql
import pandas as pd
from pandasql import sqldf

pysqldf = lambda q: sqldf(q, globals())


  Preparing metadata (setup.py) ... done


In [ ]:
df = pd.read_csv("inventory_forecasting.csv")
df.head(109500)


Date Store ID Product ID     Category Region  Inventory Level  \
0       2022-01-01     S001      P0096         Toys   West              158   
1       2022-01-01     S001      P0016     Clothing   East              189   
2       2022-01-01     S001      P0031  Electronics   West               75   
3       2022-01-01     S001      P0159  Electronics   West              161   
4       2022-01-01     S001      P0129    Furniture  South              135   
...            ...      ...        ...          ...    ...              ...   
109495  2023-12-31     S005      P0061     Clothing  South              192   
109496  2023-12-31     S005      P0085  Electronics  South              119   
109497  2023-12-31     S005      P0068  Electronics   West              131   
109498  2023-12-31     S005      P0126     Clothing  South              214   
109499  2023-12-31     S005      P0133     Clothing   East              239   

        Units Sold  Units Ordered  Demand Forecast  Price  Discount  \
0              134            142           152.36  40.88         5   
1              127            125           150.47  90.78         0   
2               48             39            68.62  13.99        20   
3               74             71            75.46  84.92        10   
4               66             69            67.18  19.66         0   
...            ...            ...              ...    ...       ...   
109495          96            111           133.44  94.32        15   
109496          89            102            91.51  72.60        10   
109497          99             95           121.82  51.38         0   
109498         112            117           153.02  90.04         0   
109499         161            192           171.80  90.71        10   

       Weather Condition  Holiday/Promotion  Competitor Pricing Seasonality  
0                  Sunny                  1               42.39      Winter  
1                  Rainy                  0               84.16      Winter  
2                  Rainy                  0               12.67      Winter  
3                  Snowy                  0               83.03      Winter  
4                 Cloudy                  0               20.55      Winter  
...                  ...                ...                 ...         ...  
109495             Sunny                  0               93.06      Winter  
109496             Snowy                  0               79.16      Winter  
109497             Rainy                  0               52.10      Winter  
109498             Sunny                  0               85.16      Winter  
109499             Rainy                  0               96.85      Winter  

[109500 rows x 15 columns]

In [ ]:
df.columns = df.columns.str.lower().str.replace(" ", "_")

In [ ]:
import sqlite3

# Create SQLite in-memory DB
conn = sqlite3.connect(":memory:")

# Load the main table
df.to_sql("inventoryforecast", conn, index=False, if_exists="replace")

109500

In [ ]:
df.rename(columns={'holiday/promotion': 'holiday_promotion'}, inplace=True)
df.columns


Index(['date', 'store_id', 'product_id', 'category', 'region',
       'inventory_level', 'units_sold', 'units_ordered', 'demand_forecast',
       'price', 'discount', 'weather_condition', 'holiday_promotion',
       'competitor_pricing', 'seasonality'],
      dtype='object')

In [ ]:
# Rename the column after normalizing
df.rename(columns={'holiday/promotion': 'holiday_promotion'}, inplace=True)

cursor = conn.cursor()
cursor.executescript("""
DROP TABLE IF EXISTS stores;
CREATE TABLE stores AS SELECT DISTINCT store_id FROM inventoryforecast;

DROP TABLE IF EXISTS regions;
CREATE TABLE regions AS SELECT DISTINCT region FROM inventoryforecast;

DROP TABLE IF EXISTS store_regions;
CREATE TABLE store_regions AS SELECT DISTINCT store_id, region FROM inventoryforecast;

DROP TABLE IF EXISTS products;
CREATE TABLE products AS
SELECT product_id, category, price, competitor_pricing FROM (
    SELECT *,
           ROW_NUMBER() OVER (PARTITION BY product_id ORDER BY date DESC, price DESC) AS rn
    FROM inventoryforecast
) WHERE rn = 1;

DROP TABLE IF EXISTS inventory_transactions;
CREATE TABLE inventory_transactions AS
SELECT NULL AS transaction_id,
       date,
       store_id,
       product_id,
       inventory_level,
       units_sold,
       units_ordered,
       demand_forecast,
       discount,
       weather_condition,
       holiday_promotion,
       seasonality
FROM inventoryforecast;
""")

In [ ]:
cursor.executescript("""
CREATE INDEX IF NOT EXISTS idx_store_id ON inventory_transactions(store_id);
CREATE INDEX IF NOT EXISTS idx_product_id ON inventory_transactions(product_id);
CREATE INDEX IF NOT EXISTS idx_date ON inventory_transactions(date);
""")

# Validate tables
validation = {
    "Stores": "SELECT COUNT(*) FROM stores",
    "Regions": "SELECT COUNT(*) FROM regions",
    "Store_Regions": "SELECT COUNT(*) FROM store_regions",
    "Products": "SELECT COUNT(*) FROM products",
    "Inventory_Transactions": "SELECT COUNT(*) FROM inventory_transactions"
}

{key: pd.read_sql(query, conn) for key, query in validation.items()}


{'Stores':    COUNT(*)
 0         5,
 'Regions':    COUNT(*)
 0         4,
 'Store_Regions':    COUNT(*)
 0        20,
 'Products':    COUNT(*)
 0        30,
 'Inventory_Transactions':    COUNT(*)
 0    109500}

In [ ]:
latest_date = df['date'].max()
q1 = (
    df[df['date'] == latest_date]
    .groupby(['store_id', 'product_id', 'category', 'region'])['inventory_level']
    .sum()
    .reset_index(name='total_inventory')
    .sort_values(['store_id', 'product_id'])
)
q1.head(150)


store_id product_id     category region  total_inventory
0       S001      P0016     Clothing  North              111
1       S001      P0017         Toys   West              147
2       S001      P0031  Electronics   East              146
3       S001      P0046     Clothing   East              218
4       S001      P0057     Clothing  North               68
..       ...        ...          ...    ...              ...
145     S005      P0171  Electronics  North              139
146     S005      P0175  Electronics   East              161
147     S005      P0178     Clothing   West              172
148     S005      P0183  Electronics  South              201
149     S005      P0187     Clothing   West              195

[150 rows x 5 columns]

from matplotlib import pyplot as plt
_df_0['total_inventory'].plot(kind='hist', bins=20, title='total_inventory')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_1.groupby('store_id').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_2.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_3.groupby('region').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_7['store_id'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_7, x='total_inventory', y='store_id', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_8['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_8, x='total_inventory', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_9['region'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_9, x='total_inventory', y='region', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
import numpy as np

q2 = df[df['date'] == latest_date].copy()

conditions = [
    q2['inventory_level'] < 0.5 * q2['demand_forecast'],
    q2['inventory_level'] < q2['demand_forecast']
]
choices = ['Critical', 'Low']
q2['stock_status'] = np.select(conditions, choices, default='Sufficient')

q2_filtered = q2[q2['inventory_level'] < q2['demand_forecast']]
q2_result = q2_filtered[[
    'store_id', 'product_id', 'category', 'inventory_level',
    'demand_forecast', 'units_sold', 'stock_status'
]].sort_values('inventory_level')

q2_result.head(24)


store_id product_id     category  inventory_level  demand_forecast  \
109406     S002      P0085  Electronics               51            55.36   
109468     S004      P0126     Clothing               67            72.15   
109366     S001      P0057     Clothing               68            85.34   
109488     S005      P0083         Toys               71            75.96   
109457     S004      P0153    Furniture               76            87.98   
109382     S002      P0031  Electronics               78            83.43   
109487     S005      P0153    Furniture               87            94.47   
109402     S002      P0149    Furniture               93            99.37   
109459     S004      P0069     Clothing               94           117.87   
109395     S002      P0178     Clothing               98           143.87   
109439     S003      P0133     Clothing              110           119.83   
109451     S004      P0183  Electronics              110           121.01   
109351     S001      P0016     Clothing              111           160.85   
109401     S002      P0017         Toys              128           134.56   
109367     S001      P0153    Furniture              128           133.45   
109372     S001      P0149    Furniture              130           137.24   
109463     S004      P0094    Groceries              136           136.67   
109477     S005      P0171  Electronics              139           151.41   
109388     S002      P0175  Electronics              139           145.71   
109445     S004      P0116    Furniture              142           157.41   
109438     S003      P0126     Clothing              163           228.41   
109460     S004      P0125     Clothing              181           188.29   
109484     S005      P0187     Clothing              195           227.84   
109456     S004      P0057     Clothing              238           261.79   

        units_sold stock_status  
109406          50          Low  
109468          55          Low  
109366          78          Low  
109488          74          Low  
109457          73          Low  
109382          71          Low  
109487          69          Low  
109402          71          Low  
109459          87          Low  
109395         103          Low  
109439         109          Low  
109451          95          Low  
109351         116          Low  
109401         114          Low  
109367          98          Low  
109372          99          Low  
109463          96          Low  
109477         106          Low  
109388         141          Low  
109445         120          Low  
109438         176          Low  
109460         140          Low  
109484         212          Low  
109456         192          Low

from matplotlib import pyplot as plt
_df_10['inventory_level'].plot(kind='hist', bins=20, title='inventory_level')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_11['demand_forecast'].plot(kind='hist', bins=20, title='demand_forecast')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_12['units_sold'].plot(kind='hist', bins=20, title='units_sold')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_13.groupby('store_id').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_26['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_26, x='inventory_level', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_27['store_id'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_27, x='demand_forecast', y='store_id', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_28['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_28, x='demand_forecast', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
# Convert the 'date' column to datetime (only once at the start)
df['date'] = pd.to_datetime(df['date'])

# Get the latest date
latest_date = df['date'].max()

# Filter last 30 days of data
recent_30 = df[df['date'] >= latest_date - pd.Timedelta(days=30)]

# Reorder Point Estimation based on last 30 days
q3 = (
    recent_30.groupby(['product_id', 'store_id', 'category'])['units_sold']
    .mean()
    .reset_index(name='avg_units_sold')
)
q3['reorder_point'] = q3['avg_units_sold'] * 1.5
q3 = q3[q3['avg_units_sold'] > 0]
q3 = q3.sort_values(by=['product_id', 'store_id'])

# Display result
q3.head(150)


product_id store_id  category  avg_units_sold  reorder_point
0        P0016     S001  Clothing      134.483871     201.725806
1        P0016     S002  Clothing      123.096774     184.645161
2        P0016     S003  Clothing      124.967742     187.451613
3        P0016     S004  Clothing      127.322581     190.983871
4        P0016     S005  Clothing      138.709677     208.064516
..         ...      ...       ...             ...            ...
145      P0187     S001  Clothing      130.290323     195.435484
146      P0187     S002  Clothing      134.419355     201.629032
147      P0187     S003  Clothing      134.903226     202.354839
148      P0187     S004  Clothing      128.419355     192.629032
149      P0187     S005  Clothing      134.322581     201.483871

[150 rows x 5 columns]

from matplotlib import pyplot as plt
_df_37['avg_units_sold'].plot(kind='hist', bins=20, title='avg_units_sold')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_38['reorder_point'].plot(kind='hist', bins=20, title='reorder_point')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_39.groupby('store_id').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_40.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_46['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_46, x='avg_units_sold', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_47['store_id'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_47, x='reorder_point', y='store_id', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_48['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_48, x='reorder_point', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
q4 = (
    recent_30.groupby(['product_id', 'category'])
    .agg({'units_sold': 'sum', 'inventory_level': 'sum'})
    .reset_index()
)
q4['turnover_ratio'] = q4['units_sold'] / q4['inventory_level'].replace(0, pd.NA)
q4 = q4.sort_values('turnover_ratio', ascending=False)
q4.head(30)


product_id     category  units_sold  inventory_level  turnover_ratio
20      P0133     Clothing       20156            27185        0.741438
5       P0061     Clothing       21028            28651        0.733936
29      P0187     Clothing       20533            28008        0.733112
18      P0126     Clothing       19943            27409        0.727608
27      P0178     Clothing       20130            27823        0.723502
6       P0066     Clothing       19860            27486        0.722550
4       P0057     Clothing       20725            28695        0.722251
3       P0046     Clothing       19886            27555        0.721684
17      P0125     Clothing       20400            28370        0.719069
9       P0069     Clothing       19105            26956        0.708748
0       P0016     Clothing       20106            28579        0.703524
11      P0079    Furniture       14885            21760        0.684053
1       P0017         Toys       14856            21752        0.682972
22      P0153    Furniture       14620            21542        0.678674
21      P0149    Furniture       14402            21235        0.678220
19      P0129    Furniture       14786            21876        0.675901
13      P0085  Electronics       13483            20153        0.669032
14      P0094    Groceries       14725            22231        0.662363
12      P0083         Toys       14760            22594        0.653271
7       P0067    Furniture       15003            22999        0.652333
8       P0068  Electronics       13905            21329        0.651929
23      P0159  Electronics       14416            22150        0.650835
10      P0070  Electronics       13150            20233        0.649928
24      P0166    Groceries       14185            21837        0.649586
16      P0116    Furniture       14967            23078        0.648540
28      P0183  Electronics       13856            21558        0.642731
25      P0171  Electronics       13853            21555        0.642682
2       P0031  Electronics       13155            20602        0.638530
15      P0096         Toys       14418            22586        0.638360
26      P0175  Electronics       13015            20476        0.635622

from matplotlib import pyplot as plt
_df_49['units_sold'].plot(kind='hist', bins=20, title='units_sold')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_50['inventory_level'].plot(kind='hist', bins=20, title='inventory_level')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_51['turnover_ratio'].plot(kind='hist', bins=20, title='turnover_ratio')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_52.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_58['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_58, x='units_sold', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_59['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_59, x='inventory_level', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_60['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_60, x='turnover_ratio', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
df['stockout_flag'] = (
    (df['units_sold'] == df['inventory_level']) &
    (df['inventory_level'] < df['demand_forecast'])
).astype(int)

q5 = (
    df.groupby(['product_id', 'category', 'store_id', 'region'])
    .agg(stockout_rate=('stockout_flag', 'mean'))
    .reset_index()
)

q5['stockout_rate'] = (q5['stockout_rate'] * 100).round(2)
q5 = q5[q5['stockout_rate'] > 0].sort_values('stockout_rate', ascending=False)
q5.head(307)


product_id     category store_id region  stockout_rate
150      P0067    Furniture     S003  South           3.15
471      P0159  Electronics     S003   West           2.35
530      P0175  Electronics     S003  South           2.16
61       P0046     Clothing     S001  North           2.07
357      P0125     Clothing     S005  North           1.94
..         ...          ...      ...    ...            ...
320      P0116    Furniture     S001   East           0.48
359      P0125     Clothing     S005   West           0.47
208      P0070  Electronics     S003   East           0.47
45       P0031  Electronics     S002  North           0.47
161      P0068  Electronics     S001  North           0.45

[307 rows x 5 columns]

from matplotlib import pyplot as plt
_df_61['stockout_rate'].plot(kind='hist', bins=20, title='stockout_rate')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_62.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_63.groupby('store_id').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_64.groupby('region').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_68['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_68, x='stockout_rate', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_69['store_id'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_69, x='stockout_rate', y='store_id', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_70['region'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_70, x='stockout_rate', y='region', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
recent_90 = df[df['date'] >= latest_date - pd.Timedelta(days=90)].copy()
recent_90['value_stock'] = recent_90['inventory_level'] * recent_90['price']
recent_90['value_sold'] = recent_90['units_sold'] * recent_90['price']

q6 = (
    recent_90.groupby(['product_id', 'category'])
    .agg(stock_value=('value_stock', 'mean'), sold_value=('value_sold', 'sum'))
    .reset_index()
)
q6['avg_inventory_age_days'] = ((q6['stock_value'] / q6['sold_value'].replace(0, pd.NA)) * 365).round(2)
q6 = q6.sort_values('avg_inventory_age_days', ascending=False)
q6.head(30)


product_id     category  stock_value  sold_value  avg_inventory_age_days
28      P0183  Electronics  7447.704198  2129677.26                    1.28
2       P0031  Electronics  7454.491604  2175204.13                    1.25
16      P0116    Furniture  8002.218264  2340250.85                    1.25
26      P0175  Electronics  7669.134571  2233690.57                    1.25
8       P0068  Electronics  7658.442505  2244225.42                    1.25
25      P0171  Electronics  7852.120681  2307812.06                    1.24
10      P0070  Electronics  7434.557253  2202227.82                    1.23
13      P0085  Electronics  7621.079275  2264940.78                    1.23
15      P0096         Toys  7774.645319  2312551.02                    1.23
19      P0129    Furniture  7513.684308  2226376.25                    1.23
24      P0166    Groceries  8261.549648  2481018.22                    1.22
23      P0159  Electronics  7588.300747  2275640.54                    1.22
7       P0067    Furniture  7879.249253  2351436.88                    1.22
1       P0017         Toys  7559.157516  2273718.04                    1.21
14      P0094    Groceries  7412.367429  2245203.16                    1.21
21      P0149    Furniture  7355.681516  2225980.05                    1.21
12      P0083         Toys  8115.434857  2460504.35                    1.20
22      P0153    Furniture  7559.578681  2318321.01                    1.19
11      P0079    Furniture  7467.686110  2284837.41                    1.19
9       P0069     Clothing  9153.475978  2869730.39                    1.16
0       P0016     Clothing  9421.672681  3017610.74                    1.14
18      P0126     Clothing  8976.418198  2877825.68                    1.14
27      P0178     Clothing  9664.623209  3105114.77                    1.14
17      P0125     Clothing  9561.689473  3078780.71                    1.13
6       P0066     Clothing  9289.012044  3005572.92                    1.13
4       P0057     Clothing  9222.673868  2989470.54                    1.13
3       P0046     Clothing  8933.290813  2904507.42                    1.12
5       P0061     Clothing  9099.331736  2966723.00                    1.12
20      P0133     Clothing  9376.735780  3076254.39                    1.11
29      P0187     Clothing  9347.157231  3063421.92                    1.11

from matplotlib import pyplot as plt
_df_71['stock_value'].plot(kind='hist', bins=20, title='stock_value')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_72['sold_value'].plot(kind='hist', bins=20, title='sold_value')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_73['avg_inventory_age_days'].plot(kind='hist', bins=20, title='avg_inventory_age_days')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_74.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_80['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_80, x='stock_value', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_81['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_81, x='sold_value', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_82['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_82, x='avg_inventory_age_days', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
q7 = df.groupby('category')['inventory_level'].mean().reset_index(name='avg_stock_level')
q7 = q7.sort_values('avg_stock_level', ascending=False)
q7.head(5)


category  avg_stock_level
0     Clothing       154.570162
3    Groceries       148.843699
4         Toys       141.789680
2    Furniture       141.703196
1  Electronics       137.203904

from matplotlib import pyplot as plt
_df_83['avg_stock_level'].plot(kind='hist', bins=20, title='avg_stock_level')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_84.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_85['avg_stock_level'].plot(kind='line', figsize=(8, 4), title='avg_stock_level')
plt.gca().spines[['top', 'right']].set_visible(False)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_86['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_86, x='avg_stock_level', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
clothing_ids = df[df['category'] == 'Clothing']['product_id'].unique()
q8 = (
    df[df['product_id'].isin(clothing_ids)]
    .groupby('weather_condition')['units_sold']
    .mean()
    .reset_index(name='avg_sales')
)
q8


weather_condition   avg_sales
0            Cloudy  105.392522
1             Rainy  105.637770
2             Snowy  105.271329
3             Sunny  105.206811

from matplotlib import pyplot as plt
q8['avg_sales'].plot(kind='hist', bins=20, title='avg_sales')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
q8.groupby('weather_condition').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
q8['avg_sales'].plot(kind='line', figsize=(8, 4), title='avg_sales')
plt.gca().spines[['top', 'right']].set_visible(False)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(q8['weather_condition'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(q8, x='avg_sales', y='weather_condition', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
q9 = df.copy()
q9['abs_error'] = (q9['units_sold'] - q9['demand_forecast']).abs()
q9 = (
    q9.groupby(['product_id', 'store_id'])
    .agg(avg_forecast_error=('abs_error', 'mean'), mape=('abs_error', lambda x: 100 * x.sum() / df['demand_forecast'].sum()))
    .reset_index()
)
q9['avg_forecast_error'] = q9['avg_forecast_error'].round(2)
q9['mape'] = q9['mape'].round(2)
q9 = q9.sort_values('mape', ascending=False)
q9.head(150)


product_id store_id  avg_forecast_error  mape
48       P0069     S004               15.94  0.10
146      P0187     S002               15.48  0.10
102      P0133     S003               15.61  0.10
145      P0187     S001               15.48  0.10
22       P0057     S003               15.53  0.10
..         ...      ...                 ...   ...
52       P0070     S003               12.14  0.07
42       P0068     S003               12.15  0.07
116      P0159     S002               11.89  0.07
131      P0175     S002               11.97  0.07
143      P0183     S004               12.10  0.07

[150 rows x 4 columns]

from matplotlib import pyplot as plt
_df_87['avg_forecast_error'].plot(kind='hist', bins=20, title='avg_forecast_error')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_88['mape'].plot(kind='hist', bins=20, title='mape')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_89.groupby('store_id').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_90.plot(kind='scatter', x='avg_forecast_error', y='mape', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
_df_92['mape'].plot(kind='line', figsize=(8, 4), title='mape')
plt.gca().spines[['top', 'right']].set_visible(False)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_93['store_id'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_93, x='avg_forecast_error', y='store_id', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_94['store_id'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_94, x='mape', y='store_id', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
df['gross_profit'] = (df['price'] - df['competitor_pricing']) * df['units_sold']
q10 = df.groupby('product_id')['gross_profit'].sum().reset_index().sort_values('gross_profit', ascending=False)
q10.head(30)


product_id  gross_profit
0       P0016      40677.25
9       P0069      39155.88
25      P0171      27507.31
29      P0187      25172.27
28      P0183      21849.12
5       P0061      20409.49
20      P0133      20255.19
8       P0068      14423.22
12      P0083      13692.46
11      P0079      12916.38
16      P0116      12099.78
2       P0031       6401.81
4       P0057       3670.82
13      P0085       3568.47
22      P0153       3472.70
10      P0070       3027.64
14      P0094        789.37
18      P0126       -128.71
17      P0125       -908.19
21      P0149      -1834.77
24      P0166      -3422.36
3       P0046      -5689.63
6       P0066      -7057.65
26      P0175     -11479.76
7       P0067     -12397.94
15      P0096     -12891.37
19      P0129     -25588.74
23      P0159     -28771.68
1       P0017     -37693.41
27      P0178     -38341.46

from matplotlib import pyplot as plt
_df_95['gross_profit'].plot(kind='hist', bins=20, title='gross_profit')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_96['gross_profit'].plot(kind='line', figsize=(8, 4), title='gross_profit')
plt.gca().spines[['top', 'right']].set_visible(False)

In [ ]:
unique_product_count = df['product_id'].nunique()
print("Unique product count:", unique_product_count)


Unique product count: 30


In [ ]:
q11 = (
    df.groupby(['product_id', 'category'])
    .agg(
        promo_sales=('units_sold', lambda x: x[df['holiday_promotion'] == 1].mean()),
        regular_sales=('units_sold', lambda x: x[df['holiday_promotion'] == 0].mean())
    )
    .reset_index()
)
q11['promo_lift_percent'] = (
    100 * (q11['promo_sales'] - q11['regular_sales']) / q11['regular_sales'].replace(0, pd.NA)
).round(2)
q11 = q11.sort_values('promo_lift_percent', ascending=False)
q11.head(30)


product_id     category  promo_sales  regular_sales  promo_lift_percent
26      P0175  Electronics   107.117338      84.864242               26.22
20      P0133     Clothing   128.607692     101.906390               26.20
27      P0178     Clothing   126.136767     101.530612               24.24
1       P0017         Toys   111.897059      90.395364               23.79
22      P0153    Furniture   110.864198      89.761596               23.51
28      P0183  Electronics   105.914498      86.289846               22.74
2       P0031  Electronics   104.716475      85.704604               22.18
6       P0066     Clothing   124.281520     101.857701               22.01
4       P0057     Clothing   124.888683     102.826744               21.46
17      P0125     Clothing   124.003690     102.293115               21.22
10      P0070  Electronics   103.009653      85.207535               20.89
7       P0067    Furniture   109.039286      90.370227               20.66
0       P0016     Clothing   123.125455     102.190323               20.49
21      P0149    Furniture   108.440154      90.144636               20.30
24      P0166    Groceries   116.372302      96.861668               20.14
11      P0079    Furniture   108.391304      90.341878               19.98
13      P0085  Electronics   102.180479      85.223045               19.90
19      P0129    Furniture   107.966972      90.144928               19.77
8       P0068  Electronics   101.279923      84.675926               19.61
18      P0126     Clothing   120.284091     101.039078               19.05
25      P0171  Electronics   102.650338      86.585023               18.55
15      P0096         Toys   107.222018      90.467633               18.52
12      P0083         Toys   106.434028      89.853286               18.45
16      P0116    Furniture   106.871795      90.384987               18.24
23      P0159  Electronics   101.598499      86.125441               17.97
9       P0069     Clothing   120.426025     102.107154               17.94
29      P0187     Clothing   121.440000     102.984640               17.92
5       P0061     Clothing   120.962366     102.577943               17.92
3       P0046     Clothing   120.949239     103.080745               17.33
14      P0094    Groceries   113.246429      97.650162               15.97

from matplotlib import pyplot as plt
_df_97['promo_sales'].plot(kind='hist', bins=20, title='promo_sales')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_98['regular_sales'].plot(kind='hist', bins=20, title='regular_sales')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_99['promo_lift_percent'].plot(kind='hist', bins=20, title='promo_lift_percent')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_100.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_106['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_106, x='promo_sales', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_107['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_107, x='regular_sales', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_108['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_108, x='promo_lift_percent', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
q12 = (
    df.groupby(['region', 'product_id', 'category'])['units_sold']
    .sum()
    .reset_index(name='total_units_sold')
    .sort_values(['region', 'total_units_sold'], ascending=[True, False])
)
q12.head(120)


region product_id     category  total_units_sold
6     East      P0066     Clothing             99610
0     East      P0016     Clothing             99305
29    East      P0187     Clothing             99083
3     East      P0046     Clothing             98690
5     East      P0061     Clothing             98193
..     ...        ...          ...               ...
118   West      P0183  Electronics             80384
115   West      P0171  Electronics             80290
98    West      P0068  Electronics             80220
100   West      P0070  Electronics             79093
92    West      P0031  Electronics             77473

[120 rows x 4 columns]

from matplotlib import pyplot as plt
_df_109['total_units_sold'].plot(kind='hist', bins=20, title='total_units_sold')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_110.groupby('region').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_111.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_112['total_units_sold'].plot(kind='line', figsize=(8, 4), title='total_units_sold')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['category'].value_counts()
    for x_label, grp in _df_113.groupby('region')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('region')
_ = plt.ylabel('category')

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_114['region'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_114, x='total_units_sold', y='region', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_115['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_115, x='total_units_sold', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [ ]:
df['month'] = df['date'].dt.to_period('M').astype(str)
q13 = (
    df.groupby(['month', 'category'])['units_sold']
    .sum()
    .reset_index(name='total_sales')
    .sort_values(['month', 'total_sales'], ascending=[True, False])
)
q13.head(120)


month     category  total_sales
0    2022-01     Clothing       219453
1    2022-01  Electronics       109141
2    2022-01    Furniture        85396
4    2022-01         Toys        43263
3    2022-01    Groceries        28575
..       ...          ...          ...
115  2023-12     Clothing       221872
116  2023-12  Electronics       108833
117  2023-12    Furniture        88663
119  2023-12         Toys        44034
118  2023-12    Groceries        28910

[120 rows x 3 columns]

from matplotlib import pyplot as plt
_df_116['total_sales'].plot(kind='hist', bins=20, title='total_sales')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_117.groupby('category').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_118['total_sales'].plot(kind='line', figsize=(8, 4), title='total_sales')
plt.gca().spines[['top', 'right']].set_visible(False)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_119['category'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_119, x='total_sales', y='category', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)